Copyright **`(c)`** 2024 Giovanni Squillero `<giovanni.squillero@polito.it>`  
[`https://github.com/squillero/computational-intelligence`](https://github.com/squillero/computational-intelligence)  
Free under certain conditions — see the [`license`](https://github.com/squillero/computational-intelligence/blob/master/LICENSE.md) for details.  

In [13]:
import logging
from itertools import combinations
import pandas as pd
import numpy as np
from geopy.distance import geodesic

from icecream import ic

logging.basicConfig(level=logging.DEBUG)

In [14]:
CITIES = pd.read_csv('cities/italy.csv', header=None, names=['name', 'lat', 'lon'])
DIST_MATRIX = np.zeros((len(CITIES), len(CITIES)))
for c1, c2 in combinations(CITIES.itertuples(), 2):
    # Here, I assign the same value to both the Turin-Milan and Milan-Turin distances
    DIST_MATRIX[c1.Index, c2.Index] = DIST_MATRIX[c2.Index, c1.Index] = geodesic(
        (c1.lat, c1.lon), (c2.lat, c2.lon)
    ).km
CITIES.head()

name    lat    lon
0   Ancona  43.60  13.50
1   Andria  41.23  16.29
2     Bari  41.12  16.87
3  Bergamo  45.70   9.67
4  Bologna  44.50  11.34

## Lab2 - TSP

https://www.wolframcloud.com/obj/giovanni.squillero/Published/Lab2-tsp.nb

In [15]:
def tsp_cost(tsp):
    # The 1st city and the last city of the route must coincide
    assert tsp[0] == tsp[-1]
    # I check that all cities have been visited
    assert set(tsp) == set(range(len(CITIES)))

    tot_cost = 0
    for c1, c2 in zip(tsp, tsp[1:]):
        tot_cost += DIST_MATRIX[c1, c2]
    return tot_cost

## Fast and approximate algorithm: Greedy Algorithm

In [16]:
visited = np.full(len(CITIES), False)
dist = DIST_MATRIX.copy()
city = 0
visited[city] = True
tsp = list()
tsp.append(int(city))
while not np.all(visited):
    dist[:, city] = np.inf
    closest = np.argmin(dist[city])
    logging.debug(
        f"step: {CITIES.at[city,'name']} -> {CITIES.at[closest,'name']} ({DIST_MATRIX[city,closest]:.2f}km)"
    )
    visited[closest] = True
    city = closest
    tsp.append(int(city))
logging.debug(
    f"step: {CITIES.at[tsp[-1],'name']} -> {CITIES.at[tsp[0],'name']} ({DIST_MATRIX[tsp[-1],tsp[0]]:.2f}km)"
)
tsp.append(tsp[0])


logging.info(f"result: Found a path of {len(tsp)-1} steps, total length {tsp_cost(tsp):.2f}km")

DEBUG:root:step: Ancona -> Rimini (90.60km)
DEBUG:root:step: Rimini -> Forlì (46.72km)
DEBUG:root:step: Forlì -> Ravenna (26.46km)
DEBUG:root:step: Ravenna -> Ferrara (66.67km)
DEBUG:root:step: Ferrara -> Bologna (43.43km)
DEBUG:root:step: Bologna -> Modena (37.29km)
DEBUG:root:step: Modena -> Reggio nell'Emilia (23.94km)
DEBUG:root:step: Reggio nell'Emilia -> Parma (26.94km)
DEBUG:root:step: Parma -> Piacenza (57.65km)
DEBUG:root:step: Piacenza -> Milan (60.65km)
DEBUG:root:step: Milan -> Monza (14.51km)
DEBUG:root:step: Monza -> Bergamo (33.92km)
DEBUG:root:step: Bergamo -> Brescia (46.02km)
DEBUG:root:step: Brescia -> Verona (61.42km)
DEBUG:root:step: Verona -> Vicenza (44.70km)
DEBUG:root:step: Vicenza -> Padua (30.13km)
DEBUG:root:step: Padua -> Venice (36.07km)
DEBUG:root:step: Venice -> Trieste (115.09km)
DEBUG:root:step: Trieste -> Bolzano (209.68km)
DEBUG:root:step: Bolzano -> Trento (49.94km)
DEBUG:root:step: Trento -> Novara (206.69km)
DEBUG:root:step: Novara -> Turin (84.46

## Slower but more accurate algorithm: Evolutionary Algorithm with inver-over crossover

In [17]:
import random
from dataclasses import dataclass

# Problem parameters:
NUM_CITIES = DIST_MATRIX.shape[0]
POPULATION_SIZE = 10
MAX_GENERATIONS = 100000  

@dataclass
class Individual:
    genome: np.ndarray
    fitness: float = None

def cost(individual):
    """Calculate the TSP route length for an individual."""
    total_distance = 0
    for i in range(len(individual)):
        city1 = individual[i]
        city2 = individual[(i + 1) % len(individual)] # Connect the last city to the first
        total_distance += DIST_MATRIX[city1][city2]
    return total_distance

def greedy_solution():
    """Generate a greedy solution to initialize the population."""
    unvisited = set(range(NUM_CITIES))
    current_city = random.choice(list(unvisited))
    genome = [current_city]
    unvisited.remove(current_city)
    
    while unvisited:
        next_city = min(unvisited, key=lambda city: DIST_MATRIX[current_city][city])
        genome.append(next_city)
        unvisited.remove(next_city)
        current_city = next_city
    
    return Individual(genome=np.array(genome), fitness=-cost(genome))

def random_solution():
    """Generate a random solution."""
    genome = np.random.permutation(NUM_CITIES)
    return Individual(genome=genome, fitness=-cost(genome))

def initialize_population():
    """Initialize the population with 9 random solutions and 1 greedy solution."""
    population = [random_solution() for _ in range(POPULATION_SIZE - 1)]
    population.append(greedy_solution())
    return population

def inver_over(individual, population, p=0.02):
    # Copy of the individual's genome to prevent direct modifications
    new_genome = individual.genome.copy()
    original_fitness = individual.fitness  # Save the original fitness for comparison
    
    # Select a random city as the starting point
    current_city = random.choice(new_genome)
    
    while True:
        # Decide how to select the city `c'`
        if random.random() < p:  # Internal mutation
            # Select a random remaining city from the genome
            next_city = random.choice([city for city in new_genome if city != current_city])
        else:  # External crossing
            # Select another random individual from the population
            other_individual = random.choice(population).genome
            current_index = list(other_individual).index(current_city)
            # `next_city` is the city following `current_city` in the second individual
            next_city = other_individual[(current_index + 1) % len(other_individual)]
        
        # Find the positions of `current_city` and `next_city` in the current genome
        current_index = list(new_genome).index(current_city)
        next_index = list(new_genome).index(next_city)
        
        # Check if `current_city` and `next_city` are already adjacent
        if abs(current_index - next_index) == 1:
            break  # Exit the loop if they are already adjacent
        
        # Reverse the subsequence between `current_city` and `next_city`
        if current_index > next_index:
            current_index, next_index = next_index, current_index
        new_genome[current_index + 1:next_index + 1] = new_genome[current_index + 1:next_index + 1][::-1]
        
        # Update `current_city` to `next_city` to continue the loop
        current_city = next_city

    # Calculate the fitness of the new solution
    new_fitness = -cost(new_genome)

    # Replace the individual in the population if the fitness has improved
    if new_fitness > original_fitness:
        # Directly update the fields of the individual in the population
        individual.genome = new_genome
        individual.fitness = new_fitness


def evolutionary_algorithm_tsp():
    population = initialize_population()

    for generation in range(MAX_GENERATIONS):
        for individual in population:
            # Create a new version of the individual using inver-over
            inver_over(individual, population, p=0.02)

        # Print the best individual of the generation
        best_individual = max(population, key=lambda individual: individual.fitness)
        print(f"Generation {generation} - Best fitness: {-best_individual.fitness}")
    
    # Return the best solution found
    best_individual = max(population, key=lambda individual: individual.fitness)
    print("Best path found:", best_individual.genome)
    print("Distance of the best path:", -best_individual.fitness)
    return best_individual

In [18]:
best_individual = evolutionary_algorithm_tsp()
None

Generation 0 - Best fitness: 4809.869177206295
Generation 1 - Best fitness: 4809.869177206295
Generation 2 - Best fitness: 4809.869177206295
Generation 3 - Best fitness: 4809.869177206295
Generation 4 - Best fitness: 4809.869177206295
Generation 5 - Best fitness: 4809.869177206295
Generation 6 - Best fitness: 4809.869177206295
Generation 7 - Best fitness: 4809.869177206295
Generation 8 - Best fitness: 4809.869177206295
Generation 9 - Best fitness: 4809.869177206295
Generation 10 - Best fitness: 4809.869177206295
Generation 11 - Best fitness: 4809.869177206295
Generation 12 - Best fitness: 4809.869177206295
Generation 13 - Best fitness: 4809.869177206295
Generation 14 - Best fitness: 4809.869177206295
Generation 15 - Best fitness: 4809.869177206295
Generation 16 - Best fitness: 4809.869177206295
Generation 17 - Best fitness: 4809.869177206295
Generation 18 - Best fitness: 4809.869177206295
Generation 19 - Best fitness: 4809.869177206295
Generation 20 - Best fitness: 4809.869177206295
Ge